In [1]:
import gym
import pylab
import random
import numpy as np
from collections import deque
import tflearn
import tensorflow as tf
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation
from keras.optimizers import Adagrad


gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=0.333)

Using TensorFlow backend.


## Task: fill empty spaces in the following agent code

In [2]:
class DeepQAgent:
    def __init__(self, state_size, action_size, render=True):
        # Tip: if you are training this on AWS the best way is to turn off rendering
        # and load it later with the serialized model
        self.render = render
        self.state_size = state_size
        self.action_size = action_size

        self.discount_factor = 0.99
        self.learning_rate = 0.001
        self.epsilon = 1.0
        self.epsilon_min = 0.005
        self.epsilon_decay = (self.epsilon - self.epsilon_min) / 50000
        self.batch_size = 64
        self.train_start = 1000
        # replay memory
        self.memory = deque(maxlen=10000)

        self.model = self.build_model()
        self.target_model = self.build_model()
        self.update_target_model()

    def build_model(self):
        model = Sequential()
        model.add(Dense(5, activation='relu', input_dim = self.state_size))
        model.add(Dense(self.action_size, activation='softmax'))
        
        adagrad = Adagrad(lr=self.learning_rate)
        model.compile(loss='categorical_crossentropy',
              optimizer=adagrad,
              metrics=['accuracy'])
        return model

    def update_target_model(self):
        print("update")
        """Update your target model to the model you are currently learning at regular time intervals"""        
        self.target_model.set_weights(self.model.get_weights())


    def get_action(self, state):
        """The choice of action uses the epsilon-greedy policy for the current network."""
        if np.random.rand() <= self.epsilon:
            if (state[0][0] < -0.6 and state[0][1] < -0.01):
                return 0
            elif (state[0][0] > -0.4 and state[0][1] > 0.01):
                return 1
            elif (state[0][0] < -0.6 and state[0][1] > -0.01):
                return 1
            elif (state[0][0] > -0.4 and state[0][1] < 0.01):
                return 0
            elif (state[0][0] > -0.6 and state[0][0] < -0.4 and state[0][1] < 0):
                return 0
            elif (state[0][0] > -0.6 and state[0][0] < -0.4 and state[0][1] > 0):
                return 1
            
            return random.randrange(self.action_size)
        else:
            q_value = self.model.predict(state)
            return np.argmax(q_value[0])

    def replay_memory(self, state, action, reward, next_state, done):
        """Save <s, a, r, s'> to replay_memory"""
        if action == 2:
            action = 1
        self.memory.append((state, action, reward, next_state, done))
        if self.epsilon > self.epsilon_min:
            self.epsilon -= self.epsilon_decay
            # print(len(self.memory))

    def train_replay(self):
        """Random sampling of batch_size samples from replay memory"""
        if len(self.memory) < self.train_start:
            return
        batch_size = min(self.batch_size, len(self.memory))
        mini_batch = random.sample(self.memory, batch_size)

        update_input = np.zeros((batch_size, self.state_size))
        update_target = np.zeros((batch_size, self.action_size))

        for i in range(batch_size):
            state, action, reward, next_state, done = mini_batch[i]
            target = self.model.predict(state)[0]
            print(state, action, reward, next_state, done)

            # As in queuing, it gets the maximum Q Value at s'. However, it is imported from the target model.
            if done:
                target[action] = reward
            else:
                target[action] = reward + self.discount_factor * \
                                          np.amax(self.target_model.predict(next_state)[0])
            update_input[i] = state
            update_target[i] = target

        print('input', update_input)
        print('target', update_target)
        # You can create a minibatch of the correct target answer and the current value of your own,
        self.model.fit(update_input, update_target, batch_size=batch_size, epochs=1, verbose=0)

    def load_model(self, name):
        self.model.load_model(name)

    def save_model(self, name):
        self.model.save(name)


In [3]:
env = gym.make('MountainCar-v0')
state_size = env.observation_space.shape[0] # should be equal 2
ACTION_SIZE = 2
agent = DeepQAgent(state_size, ACTION_SIZE)
#agent.load_model("./save_model/model")
scores, episodes = [], []
N_EPISODES = 4000

update


In [4]:
for e in range(N_EPISODES):
    done = False
    score = 0
    state = env.reset()
    state = np.reshape(state, [1, state_size])
    print("state", state)

    # Action 0 (left), 1 (do nothing), 3 (declare fake_action to avoid doing nothing
    fake_action = 0

    # Counter for the same action 4 times
    action_count = 0

    while not done:
        if agent.render:
            env.render()

        # Select an action in the current state and proceed to a step
        action_count = action_count + 1

        if action_count == 4:
            action = agent.get_action(state)
            action_count = 0

            if action == 0:
                fake_action = 0
            elif action == 1:
                fake_action = 2

        # Take 1 step with the selected action
        next_state, reward, done, info = env.step(fake_action)
        next_state = np.reshape(next_state, [1, state_size])
        # Give a penalty of -100 for actions that end an episode
        # reward = reward if not done else -100

        # Save <s, a, r, s'> to replay memory
        agent.replay_memory(state, fake_action, reward, next_state, done)
        # Continue to learn every time step
        agent.train_replay()
        score += reward
        state = next_state

        if done:
            env.reset()
            # Copy the learning model for each episode to the target model
            agent.update_target_model()

            # For each episode, the time step where cartpole stood is plot
            scores.append(score)
            episodes.append(e)
            print("episode:", e, "  score:", score, "  memory length:", len(agent.memory),
                  "  epsilon:", agent.epsilon)

    # Save model for every 50 episodes
    if e % 50 == 0:
        agent.save_model("./save_model/model")

state [[-0.51292625  0.        ]]
update
episode: 0   score: -145.0   memory length: 145   epsilon: 0.9971145000000056
state [[-0.57269462  0.        ]]
update
episode: 1   score: -125.0   memory length: 270   epsilon: 0.9946270000000104
state [[-0.45210228  0.        ]]
update
episode: 2   score: -96.0   memory length: 366   epsilon: 0.992716600000014
state [[-0.43607884  0.        ]]
update
episode: 3   score: -160.0   memory length: 526   epsilon: 0.9895326000000202
state [[-0.51138465  0.        ]]
update
episode: 4   score: -145.0   memory length: 671   epsilon: 0.9866471000000258
state [[-0.47735087  0.        ]]
update
episode: 5   score: -154.0   memory length: 825   epsilon: 0.9835825000000317
state [[-0.57140011  0.        ]]
update
episode: 6   score: -125.0   memory length: 950   epsilon: 0.9810950000000365
state [[-0.4681253  0.       ]]
input [[ -8.03692241e-01   1.79097543e-02]
 [ -3.43314776e-01   3.31606789e-02]
 [  2.98929275e-01   4.94220395e-02]
 [ -7.39628354e-01  

input [[ -5.79527699e-01   1.03506611e-02]
 [ -6.04455371e-01  -5.67096676e-03]
 [  3.47791007e-01   4.88617321e-02]
 [ -4.28596242e-01  -3.73094439e-02]
 [ -6.87714491e-01  -6.01791276e-02]
 [ -4.46707659e-02   3.60545927e-02]
 [ -7.71726764e-01  -7.01272307e-03]
 [ -4.61238892e-01  -4.55148189e-03]
 [  4.91572964e-01   1.35283257e-02]
 [ -1.20000000e+00   0.00000000e+00]
 [ -1.02395668e+00   3.28717895e-02]
 [ -5.68422855e-01  -9.51199668e-03]
 [ -6.19166862e-01  -9.49362344e-04]
 [ -2.49965107e-01   6.16499743e-02]
 [ -4.77892623e-01   3.78141057e-02]
 [  7.86151468e-02   1.15380805e-02]
 [  1.11544805e-01   7.21075264e-04]
 [ -3.70407962e-02   5.76617441e-02]
 [  4.07687077e-02   1.60779151e-02]
 [ -8.48331664e-01  -2.92794348e-03]
 [  4.13598677e-02  -1.98719780e-02]
 [ -5.98601680e-01   7.40863383e-03]
 [ -6.18705461e-01   5.80959019e-02]
 [ -5.49585875e-01  -4.15469669e-02]
 [ -1.46451112e-01  -3.30424233e-04]
 [ -2.62835686e-01   1.75384438e-02]
 [ -1.00820969e+00   3.42556634e

input [[ -5.14006276e-01  -1.08003030e-03]
 [  6.44954125e-02  -1.62191817e-02]
 [  7.76458854e-02  -1.29815584e-02]
 [ -1.85921260e-01   2.99994674e-02]
 [ -4.39420241e-01   3.84723827e-02]
 [  1.30849749e-02   4.75329958e-02]
 [ -5.39674537e-01   1.44286784e-02]
 [  4.75314528e-01   4.90140397e-02]
 [ -2.78751764e-01   3.25135954e-02]
 [ -2.49965107e-01   6.16499743e-02]
 [ -1.16038837e+00  -5.94529446e-02]
 [ -4.48427008e-01  -6.40555182e-02]
 [ -7.72677583e-01   3.84481450e-03]
 [  4.65175719e-01   1.23048522e-02]
 [ -5.74589253e-01  -1.26152591e-03]
 [ -7.58573735e-01   9.15735881e-03]
 [ -7.16153349e-01  -1.73858980e-02]
 [ -9.24768430e-01  -3.87277268e-02]
 [ -5.78522889e-01   3.37480259e-02]
 [ -1.18151372e+00   9.01445536e-03]
 [ -5.78599683e-01  -1.01768283e-02]
 [  2.29843966e-02   3.30781543e-02]
 [  1.88821129e-01   4.19329610e-02]
 [ -3.56111665e-01   1.97516903e-02]
 [ -6.43531495e-01   5.73569091e-02]
 [  4.45066884e-01   4.86724163e-02]
 [ -8.58059670e-01   4.64899995e

input [[-0.67425417 -0.01254311]
 [-0.57667911 -0.01601848]
 [-0.49494917  0.04182497]
 [-0.53374019 -0.00626647]
 [-0.63264843 -0.05985423]
 [-0.67680136  0.05598691]
 [ 0.38879986  0.04885277]
 [-0.57895556 -0.00248571]
 [ 0.22964458  0.04082345]
 [-0.2460595   0.01677618]
 [ 0.37756703  0.048794  ]
 [ 0.08017989  0.01168359]
 [-0.64907354 -0.01260142]
 [ 0.47531453  0.04901404]
 [-0.75253562 -0.05983632]
 [ 0.23262219  0.01023955]
 [-0.39878673 -0.05472456]
 [-0.72361413  0.03106774]
 [-0.74265118 -0.01526688]
 [-0.98318294 -0.0558535 ]
 [-0.56758928 -0.05927505]
 [ 0.00711973  0.01907049]
 [-1.19252817  0.00374203]
 [-0.73888916 -0.0183405 ]
 [-1.01753633  0.03365551]
 [-0.35660782 -0.06112595]
 [ 0.31930161  0.01223748]
 [ 0.08872243  0.01010729]
 [ 0.04135987 -0.01987198]
 [-1.02395668  0.03287179]
 [-0.10595607  0.03340082]
 [-0.69564367 -0.01627259]
 [ 0.2561643  -0.0027375 ]
 [-0.49295036 -0.01219917]
 [ 0.02167292 -0.02314996]
 [-0.64436172  0.03020476]
 [-0.86529259 -0.00363

input [[ -3.36563935e-01   1.95477301e-02]
 [ -3.95687141e-01   1.97597516e-02]
 [ -7.81027436e-01  -1.53213035e-02]
 [ -5.46524169e-01  -1.18575591e-02]
 [  8.01798862e-02   1.16835925e-02]
 [ -1.19675810e+00   3.24189604e-03]
 [ -1.89992654e-01  -4.37157532e-02]
 [ -1.19875810e+00   1.24189604e-03]
 [  6.26667531e-03   1.89303834e-02]
 [ -5.38611076e-01   3.00349712e-02]
 [ -9.50376089e-01  -6.45542657e-02]
 [ -8.86040704e-01  -3.99411942e-02]
 [ -6.15752219e-01   2.35048085e-03]
 [ -4.97094516e-01  -8.12183138e-03]
 [ -4.33427219e-02   3.05872938e-02]
 [ -6.61755964e-01  -1.26824281e-02]
 [ -4.67608597e-01  -3.90123558e-02]
 [ -6.54854854e-01   3.04849959e-02]
 [  7.86151468e-02   1.15380805e-02]
 [ -5.19366004e-01  -3.20776349e-03]
 [  1.99745560e-01  -1.71415023e-02]
 [ -2.28901718e-01   1.59003840e-02]
 [ -5.04924711e-01  -1.13272678e-02]
 [ -6.76801363e-01   5.59869103e-02]
 [  3.11406428e-02   5.59408431e-02]
 [ -6.06010314e-01   5.79682483e-03]
 [ -6.18102700e-01   6.51158488e

...

input [[ -1.03264067e+00  -3.45023998e-02]
 [ -2.66664320e-02   2.59458869e-02]
 [ -4.92950361e-01  -1.21991688e-02]
 [ -5.95840401e-01  -1.22329016e-02]
 [ -4.13001289e-01  -5.62880571e-03]
 [ -1.19627021e+00   2.48789825e-03]
 [ -8.58059670e-01   4.64899995e-02]
 [ -2.08879469e-01   4.40439803e-02]
 [ -5.88236224e-01   3.41744565e-02]
 [ -8.45251247e-01  -4.09541053e-02]
 [ -5.35737714e-01  -1.30037191e-02]
 [ -1.01353508e+00  -6.31589883e-02]
 [ -4.68530796e-01   0.00000000e+00]
 [ -6.64434503e-01   3.07147228e-02]
 [ -8.62055951e-03   2.34748429e-02]
 [ -5.64902346e-01  -8.24041752e-03]
 [ -5.84294373e-01   5.92371224e-02]
 [  3.69089388e-01   2.42396083e-02]
 [ -1.11558684e+00  -5.69999424e-02]
 [ -8.78147352e-02  -3.99158880e-02]
 [  7.76458854e-02  -1.29815584e-02]
 [ -4.78696616e-01  -1.34574754e-03]
 [ -1.19415488e+00  -5.87675332e-02]
 [ -2.55684565e-01   1.74659545e-02]
 [ -1.20000000e+00   0.00000000e+00]
 [ -1.11209123e+00   2.24371544e-02]
 [  4.94155745e-01   4.90888607e

input [[ 0.09350671 -0.00938984]
 [-1.05682847  0.02937283]
 [-0.64353149  0.05735691]
 [-0.25330151  0.03925491]
 [-0.71168246 -0.01603879]
 [-0.19459376 -0.01674786]
 [-0.84504677 -0.01090727]
 [-0.68842497  0.02837342]
 [-0.43772772 -0.00164888]
 [-0.82100182  0.0257477 ]
 [ 0.06123185 -0.01641404]
 [-1.19627021  0.0024879 ]
 [-0.47694544 -0.00419169]
 [ 0.00931724  0.02670201]
 [-0.70798974 -0.02193543]
 [-0.61770101 -0.00274928]
 [-0.35607978 -0.03351014]
 [ 0.24341774  0.01283792]
 [-0.26905092  0.03435234]
 [ 0.06022792 -0.01403688]
 [-0.9231358  -0.05742253]
 [-0.63420378 -0.04277653]
 [-0.46980966 -0.00285619]
 [-0.70252734 -0.06303174]
 [-0.03460799 -0.04575353]
 [-0.03459635 -0.03660103]
 [ 0.09535509  0.0539765 ]
 [-0.52658228 -0.01165739]
 [-0.57269462  0.        ]
 [-1.2         0.        ]
 [-0.57785009  0.03057535]
 [-0.33736302  0.06232178]
 [-0.10595607  0.03340082]
 [-0.14484972  0.00592506]
 [-0.91493586 -0.01136625]
 [-0.15385782 -0.00715436]
 [-0.58087502 -0.00311

input [[-1.03827616  0.03150456]
 [-0.04467077  0.03605459]
 [-0.43597114  0.06187089]
 [-0.67937108 -0.01639882]
 [-0.5543848  -0.01330633]
 [-0.15703308  0.04005376]
 [-0.99195579 -0.06608909]
 [-0.58304054 -0.0147719 ]
 [ 0.06449541 -0.01621918]
 [-1.17113921 -0.05555238]
 [-1.2         0.        ]
 [-0.51212862 -0.06799481]
 [-0.23462393 -0.05662496]
 [-0.48665179 -0.0069563 ]
 [-0.93440519  0.00301739]
 [-0.56775954  0.01176816]
 [-0.15753457 -0.00677533]
 [-0.27805968  0.03238158]
 [-0.54215937 -0.00711428]
 [-1.13122662  0.01978931]
 [-1.2         0.        ]
 [-0.5286411  -0.01147518]
 [-0.16425057 -0.01039274]
 [-0.23013256  0.01592694]
 [-0.57025597  0.02874913]
 [ 0.44176537  0.02438546]
 [-0.37754753  0.03334228]
 [-0.2460595   0.01677618]
 [-1.05682847  0.02937283]
 [-0.86943578  0.01953341]
 [-0.15690757  0.0287367 ]
 [ 0.07034523  0.01752188]
 [-0.93707432 -0.00371307]
 [-0.85967755 -0.01182877]
 [-0.80365378 -0.01322587]
 [ 0.10369404  0.04457414]
 [-0.68956435  0.02288

input [[-0.08384806 -0.04924007]
 [ 0.27677174  0.02710033]
 [-0.52360551 -0.00423951]
 [ 0.01964616  0.02921456]
 [-1.16919949  0.01231423]
 [-0.57776064 -0.01028559]
 [ 0.32033289  0.02494865]
 [-0.97047111  0.03773858]
 [-1.1987581   0.0012419 ]
 [-0.31338435 -0.06187085]
 [ 0.34737064  0.03866503]
 [-0.44054881 -0.01089985]
 [-0.19997019  0.01396449]
 [-0.81667299  0.01228127]
 [-0.55056443 -0.00952282]
 [ 0.06123185 -0.01641404]
 [-0.26905092  0.03435234]
 [-0.26242569  0.06196016]
 [-0.61486063  0.025245  ]
 [-0.29161996 -0.04983944]
 [-0.92726041  0.00951572]
 [-0.56775954  0.01176816]
 [ 0.42630049  0.04873346]
 [-1.19052817  0.00574203]
 [-0.85681007 -0.01573006]
 [ 0.24194621  0.00932402]
 [-0.91493586 -0.01136625]
 [-1.09779103  0.02453904]
 [-1.08620131  0.02588993]
 [-0.15376406  0.06030022]
 [-0.21485885  0.03844266]
 [-0.63949561 -0.06288356]
 [-0.0095684   0.03071353]
 [ 0.02074139  0.02295394]
 [-0.4681253   0.        ]
 [-0.87876919 -0.06253325]
 [-0.15688807 -0.00684

KeyboardInterrupt: 